# Building a DST chatbot

In [1]:
# Import necessary libraries
from datetime import datetime
import re  # for basic entity extraction
import ollama  # for interfacing with Llama hosted on Ollama
from collections import defaultdict

In [2]:
!ollama pull mistral

pulling manifest ⠋ pulling manifest ⠙ pulling manifest ⠹ pulling manifest ⠸ pulling manifest ⠼ pulling manifest ⠴ pulling manifest 
pulling ff82381e2bea... 100% ▕████████████████▏ 4.1 GB                         
pulling 43070e2d4e53... 100% ▕████████████████▏  11 KB                         
pulling 491dfa501e59... 100% ▕████████████████▏  801 B                         
pulling ed11eda7790d... 100% ▕████████████████▏   30 B                         
pulling 42347cd80dc8... 100% ▕████████████████▏  485 B                         
verifying sha256 digest 
writing manifest 
success 


## Load dataset

In [3]:
from datasets import load_dataset

# Load MultiWOZ 2.2 dataset with trust_remote_code
dataset = load_dataset("multi_woz_v22")

# Inspect the dataset
print(dataset)

DatasetDict({
    train: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 8437
    })
    validation: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 1000
    })
    test: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 1000
    })
})


In [4]:
train_data = dataset['train']
validation_data = dataset['validation']
test_data = dataset['test']

print(train_data[0])

{'dialogue_id': 'PMUL4398.json', 'services': ['restaurant', 'hotel'], 'turns': {'turn_id': ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11'], 'speaker': [0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1], 'utterance': ['i need a place to dine in the center thats expensive', 'I have several options for you; do you prefer African, Asian, or British food?', 'Any sort of food would be fine, as long as it is a bit expensive. Could I get the phone number for your recommendation?', 'There is an Afrian place named Bedouin in the centre. How does that sound?', 'Sounds good, could I get that phone number? Also, could you recommend me an expensive hotel?', "Bedouin's phone is 01223367660. As far as hotels go, I recommend the University Arms Hotel in the center of town.", 'Yes. Can you book it for me?', 'Sure, when would you like that reservation?', 'i want to book it for 2 people and 2 nights starting from saturday.', 'Your booking was successful. Your reference number is FRGZWQL2 . May I help you

## Build the dialog state feature and simple chatbot

In [139]:
import json
from datetime import datetime
import re
import requests  # Assuming you are using requests for API calls

# Define the SearchQuery class if not already defined
class SearchQuery:
    def __init__(self, query, date):
        self.query = query
        self.date = date

    def to_dict(self):
        return {"query": self.query, "date": self.date}

# Define the DialogueTurn class with the updated to_json method
class DialogueTurn:
    def __init__(self, agent_utterance=None, user_utterance=None, initial_search_query=None, intent=None, turn_log=None):
        self.agent_utterance = agent_utterance
        self.user_utterance = user_utterance
        self.initial_search_query = initial_search_query
        self.intent = intent  # Add intent as an attribute
        self.turn_log = turn_log

    def to_json(self):
        # Convert `SearchQuery` to a dictionary if it exists
        data = self.__dict__.copy()
        if isinstance(self.initial_search_query, SearchQuery):
            data["initial_search_query"] = self.initial_search_query.to_dict()
        return json.dumps(data)


# Define the DialogState class to maintain conversation state
class DialogState:
    def __init__(self, train_data):
        self.history = []  # Conversation history
        self.current_intent = None  # Current user intent
        self.entities = {}  # Extracted entities
        self.context = {}  # Contextual information (e.g., preferences, known user info)
        self.session_active = True  # Manage session state
        self.timestamp = datetime.now()
        self.train_data = train_data  # Training data (MultiWOZ)
        self.slots = defaultdict(dict)  # Slots associated with each intent
        self.retrieved_results = {}  # Evidence (retrieved information) for each intent
        self.goal = defaultdict(lambda: {"info": {}, "reqt": [], "book": {}})
        self.history = []  # Log of user and system turns

    def update_retrieved_results(self, intent, evidence):
        """
        Store evidence retrieved for the given intent.
        """
        self.retrieved_results[intent] = evidence

    def get_retrieved_results(self, intent):
        """
        Retrieve stored evidence for a given intent.
        """
        return self.retrieved_results.get(intent, "No evidence found.")


    def update_goal(self, intent, entities):
        """
        Update the goal with the extracted intent and entities.
        """
        if intent in self.goal:
            self.goal[intent]["info"].update(entities)

    def add_to_history(self, speaker, utterance):
        """
        Add a turn to the history (log) with the speaker explicitly labeled.
        """
        self.history.append({"speaker": speaker, "utterance": utterance})

    def get_goal(self):
        """
        Retrieve the goal structure.
        """
        return dict(self.goal)

    def get_log(self):
        """
        Retrieve the dialogue history as a log.
        """
        return self.history

    def update_intent(self, user_input):
        # Convert input to lowercase for consistent matching
        user_input = user_input.lower()
        
        # Check specific intents first
        if "change" in user_input or "modify" in user_input or "reschedule" in user_input or "later time" in user_input:
            self.current_intent = "modify_reservation"
        elif "cancel" in user_input or "remove" in user_input or "delete" in user_input:
            self.current_intent = "cancel_reservation"
        elif "confirm" in user_input or "verify" in user_input:
            self.current_intent = "confirm_reservation"
        elif "reserve" in user_input or "book" in user_input or "schedule" in user_input:
            self.current_intent = "reservation_request"
        elif "feedback" in user_input or "review" in user_input or "rate" in user_input:
            self.current_intent = "provide_feedback"
        elif "refund" in user_input or "money back" in user_input:
            self.current_intent = "request_refund"
        elif "support" in user_input or "help" in user_input or "assistance" in user_input:
            self.current_intent = "contact_support"
        elif "complaint" in user_input or "issue" in user_input:
            self.current_intent = "file_complaint"
        elif "payment" in user_input or "card" in user_input or "pay" in user_input:
            self.current_intent = "query_payment_options"
        elif "receipt" in user_input or "invoice" in user_input or "proof of purchase" in user_input:
            self.current_intent = "request_receipt"
        elif "pet" in user_input or "animal" in user_input:
            self.current_intent = "query_pet_policy"
        elif "loyalty" in user_input or "points" in user_input or "rewards" in user_input:
            self.current_intent = "query_loyalty_program"
        # train ticketing intents
        elif "price" in user_input or "cost" in user_input or "fare" in user_input:
            self.current_intent = "query_price"
        elif "discount" in user_input or "offer" in user_input or "deal" in user_input:
            self.current_intent = "query_discount"
        elif "child" in user_input or "kids" in user_input or "family" in user_input:
            self.current_intent = "query_child_fare_policy"
        elif "return ticket" in user_input or "round trip" in user_input or "two-way" in user_input:
            self.current_intent = "add_return_ticket"
        elif "train" in user_input or "departure" in user_input or "arrival" in user_input or "timing" in user_input or "schedule" in user_input:
            self.current_intent = "train_schedule"
        elif "platform" in user_input or "boarding" in user_input or "gate" in user_input:
            self.current_intent = "query_platform"
        elif "seat" in user_input or "class" in user_input or "upgrade" in user_input:
            self.current_intent = "select_seat"
        elif "delay" in user_input or "status" in user_input or "late" in user_input:
            self.current_intent = "train_status"
        elif "duration" in user_input or "how long" in user_input or "travel time" in user_input:
            self.current_intent = "query_duration"
        elif "baggage" in user_input or "luggage" in user_input:
            self.current_intent = "query_baggage_policy"
        elif "station" in user_input or "location" in user_input or "where" in user_input:
            self.current_intent = "query_station_location"
        elif "accessibility" in user_input or "wheelchair" in user_input or "assistance" in user_input:
            self.current_intent = "request_accessibility_info"
        # intents from MultiWOZ
        elif "restaurant" in user_input or "dining" in user_input:
            self.current_intent = "find_restaurant"
        elif "hotel" in user_input or "stay" in user_input or "accommodation" in user_input:
            self.current_intent = "find_hotel"
        elif "attraction" in user_input or "sightseeing" in user_input:
            self.current_intent = "find_attraction"
        elif "hospital" in user_input or "emergency" in user_input or "medical" in user_input:
            self.current_intent = "find_hospital"
        elif "taxi" in user_input or "cab" in user_input:
            self.current_intent = "find_taxi"
        elif "bus" in user_input or "public transport" in user_input:
            self.current_intent = "find_bus"
        elif "train" in user_input or "railway" in user_input:
            self.current_intent = "find_train"
        elif "book restaurant" in user_input:
            self.current_intent = "book_restaurant"
        elif "book hotel" in user_input:
            self.current_intent = "book_hotel"
        elif "book train" in user_input:
            self.current_intent = "book_train"
        # any other general inquiries
        else:
            self.current_intent = "general_inquiry"

    def fill_slots(self, intent, user_input):
        # Mock slot filling
        if intent == "find_restaurant":
            if "center" in user_input:
                self.slots[intent]["restaurant-area"] = "center"
            if "cheap" in user_input:
                self.slots[intent]["restaurant-pricerange"] = "cheap"
        elif intent == "find_hotel":
            if "5-star" in user_input:
                self.slots[intent]["hotel-stars"] = "5-star"
            if "parking" in user_input:
                self.slots[intent]["hotel-parking"] = "yes"
        elif intent == "find_taxi":
            if "downtown" in user_input:
                self.slots[intent]["taxi-destination"] = "downtown"
        elif intent == "find_train":
            if "morning" in user_input:
                self.slots[intent]["train-leaveat"] = "morning"
        return self.slots[intent]        


    def extract_entities(self, user_input):
        # Extract relevant entities for restaurant reservations
        # Number of guests or passengers
        guests = re.search(r'\b(\d+)\s*(?:guests|people|persons|passengers)?', user_input)
        if guests:
            self.entities["num_guests"] = int(guests.group(1))

        # Date in different formats
        date_match = re.search(r'\b(\d{1,2}/\d{1,2}/\d{4})\b', user_input)  # mm/dd/yyyy
        if not date_match:
            date_match = re.search(r'\b(\d{1,2}-\d{1,2}-\d{4})\b', user_input)  # mm-dd-yyyy
        if date_match:
            self.entities["date"] = date_match.group(1)

        # Time in different formats, including 24-hour time
        time_match = re.search(r'\b(\d{1,2}:\d{2}\s*(?:AM|PM)?)\b', user_input, re.IGNORECASE)  # 12-hour format
        if not time_match:
            time_match = re.search(r'\b(\d{1,2}:\d{2})\b', user_input)  # 24-hour format
        if time_match:
            self.entities["time"] = time_match.group(1)

        # Departure and destination locations
        # Use regex to correctly capture 'departure' and 'destination' locations only
        departure_match = re.search(r'\bfrom\s+([A-Za-z\s]+?)(?=\s+to\b)', user_input, re.IGNORECASE)
        destination_match = re.search(r'\bto\s+([A-Za-z\s]+(?:\s+[A-Za-z\s]+)?)', user_input, re.IGNORECASE)
        day_match = re.search(r'\b(monday|tuesday|wednesday|thursday|friday|saturday|sunday)\b', user_input, re.IGNORECASE)
        if departure_match:
            self.entities["departure"] = departure_match.group(1).strip()
        if destination_match:
            self.entities["destination"] = destination_match.group(1).strip()
        if day_match:
            self.entities["day"] = day_match.group(1).capitalize()  # Capitalize to match dataset

        # Seat preference (window, aisle, quiet car)
        seat_preference = re.search(r'(window|aisle|quiet)', user_input, re.IGNORECASE)
        if seat_preference:
            self.entities["seat_preference"] = seat_preference.group(0).lower()

        # Discount type, e.g., student discount
        discount = re.search(r"(student|senior|military)\s+discount", user_input, re.IGNORECASE)
        if discount:
            self.entities["discount_type"] = discount.group(1).lower()

        # Wi-Fi preference
        wifi_preference = re.search(r'Wi-Fi|internet', user_input, re.IGNORECASE)
        if wifi_preference:
            self.entities["wifi"] = True

        # Confirm if user asked for a return ticket
        if "return ticket" in user_input or "round trip" in user_input:
            self.entities["return_ticket"] = True

        
    def update_context(self, user_input, bot_response):
        """
        Update the dialog context with the last response and intent.
        """
        self.context = {
            "last_response": bot_response,
            "last_intent": self.current_intent
        }

    def update_state(self, user_input, bot_response):
        """
        Main method to update intent, entities, and context dynamically for each turn.
        """
        self.update_intent(user_input)
        self.extract_entities(user_input)
        self.update_context(user_input, bot_response)

    def get_current_state(self):
        # Retrieve a summary of the current dialog state
        return {
            "intent": self.current_intent,
            "entities": self.entities,
            "context": self.context,
            "history": self.history,
            "timestamp": self.timestamp
        }


class Chatbot:
    SYSTEM_PROMPT = (
        "You are an intelligent assistant capable of handling a variety of tasks, "
        "including hotel and restaurant reservations, providing information on local attractions, "
        "and assisting with taxi and train bookings. Your role includes understanding user requests, "
        "identifying key details, and providing helpful, accurate responses. "
        "Ask clarifying questions if needed, and adapt your responses based on the context of each request. "
        "The current date is 11/5/2024. Please maintain a friendly and helpful tone throughout."
    )

    def __init__(self, dialog_state):
        self.dialog_state = dialog_state
        self.api_url = "http://localhost:11434/api/generate"
        self.dialogue_turns = []  # Store dialogue turns
        self.output_file = "chatbot_output.json"  # File to save dialogues
        self.turn_counter = 0  # Initialize a turn counter
        self.dialogue_counter = 0  # Initialize a dialogue counter
        self.intent_schema = {
            "find_restaurant": [
                "restaurant-pricerange", "restaurant-name", "restaurant-food",
                "restaurant-area", "restaurant-booktime", "restaurant-bookpeople"
            ],
            "find_hotel": [
                "hotel-area", "hotel-stars", "hotel-internet", "hotel-name",
                "hotel-pricerange", "hotel-type", "hotel-parking"
            ],
            "book_hotel": [
                "hotel-bookstay", "hotel-bookpeople", "hotel-area", "hotel-stars",
                "hotel-internet", "hotel-name", "hotel-bookday", "hotel-pricerange",
                "hotel-type", "hotel-parking"
            ],
            "book_restaurant": [
                "restaurant-bookday", "restaurant-pricerange", "restaurant-name",
                "restaurant-food", "restaurant-area", "restaurant-booktime",
                "restaurant-bookpeople"
            ],
            "find_taxi": [
                "taxi-destination", "taxi-arriveby", "taxi-leaveat", "taxi-departure"
            ],
            "find_train": [
                "train-day", "train-departure", "train-arriveby", "train-bookpeople",
                "train-destination", "train-leaveat"
            ],
            "book_train": [
                "train-day", "train-departure", "train-bookpeople", "train-arriveby",
                "train-destination", "train-leaveat"
            ],
            "find_attraction": [
                "attraction-area", "attraction-type", "attraction-name"
            ],
            "find_hospital": ["hospital-department"],
            "find_bus": ["bus-leaveat", "bus-day", "bus-departure", "bus-destination"]
        }

    def retrieve_from_database(self, intent, slots):
        """
        Simulate retrieval logic and generate mock evidence.
        """
        evidence = f"Mock data retrieved for intent '{intent}' with details: {slots}"
        # Store the retrieved evidence in DialogState
        self.dialog_state.update_retrieved_results(intent, evidence)
        return evidence

    def process_input(self, user_input, is_new_dialogue=False):
        """
        Processes user input by detecting intent, filling slots, retrieving evidence, and generating responses.
        """
        # If this is a new dialogue, reset turn_counter and increment dialogue_counter
        if is_new_dialogue:
            self.turn_counter = 0
            if len(self.dialogue_turns) == 0:  # First dialogue
                self.dialogue_counter = 0
            else:
                self.dialogue_counter += 1

        # Step 1: Detect intent
        self.dialog_state.update_intent(user_input)
        intent = self.dialog_state.current_intent

        # Step 2: Extract entities & Fill slots
        self.dialog_state.extract_entities(user_input)
        filled_slots = self.dialog_state.fill_slots(intent, user_input)
        missing_slots = [slot for slot, value in filled_slots.items() if value is None]

        if missing_slots:
            # Ask for missing information
            bot_response = f"I need more information: {', '.join(missing_slots)}."
        else:
            # Step 3: Retrieve evidence and store it
            evidence = self.retrieve_from_database(intent, filled_slots)

            # Step 4: Generate response using LLM
            headers = {'Content-Type': 'application/json'}
            prompt = f"{Chatbot.SYSTEM_PROMPT}\nUser: {user_input}\nAssistant:"

            # Generate response from LLM
            data = {
                'model': 'mistral',
                'prompt': prompt
            }
            response = requests.post(self.api_url, headers=headers, data=json.dumps(data), stream=True)
            bot_reply = ""

            if response.status_code == 200:
                for line in response.iter_lines():
                    if line:
                        try:
                            line_data = json.loads(line)
                            bot_reply += line_data.get("response", "")
                        except json.JSONDecodeError:
                            bot_reply = "I'm having trouble generating a response."
                            break
            else:
                bot_reply = "I'm having trouble generating a response."

            bot_response = f"{bot_reply}\n\nEvidence: {evidence}"

        # Step 5: Log the current state and response
        self.dialog_state.update_state(user_input, bot_response)

        # Step 6: Log the dialogue turn
        dialogue_id = self.dialogue_counter  # Use integer dialogue ID
        
        # Increment the turn counter for user turn
        user_turn = {
            "dialogue_id": dialogue_id,
            "turn_id": self.turn_counter,
            "speaker": "user",
            "utterance": user_input,
            "frames": [
                {
                    "intent": intent,
                    "slots": filled_slots,
                    "entities": self.dialog_state.entities.copy(),
                    "context": self.dialog_state.context
                }
            ]
        }
        self.dialogue_turns.append(user_turn)
        self.turn_counter += 1  # Increment for the next turn

        # Increment the turn counter for system turn
        system_turn = {
            "dialogue_id": dialogue_id,
            "turn_id": self.turn_counter,
            "speaker": "system",
            "utterance": bot_response,
            "frames": []
        }
        self.dialogue_turns.append(system_turn)
        self.turn_counter += 1  # Increment for the next turn

        # Save to JSON file
        self.save_to_json()

        return bot_response


    def save_to_json(self):
        """
        Saves all dialogue turns to a JSON file in the desired structure.
        """
        with open(self.output_file, 'w') as outfile:
            json.dump(self.dialogue_turns, outfile, indent=4)

    def get_dialogue_state(self):
        """
        Retrieve current dialog state details.
        """
        return self.dialog_state.get_current_state()

    def get_dialogue_turns(self):
        """
        Retrieve all dialogue turns in transformed structure.
        """
        return self.dialogue_turns

    def get_goal(self):
        return self.dialog_state.get_goal()

    def get_log(self):
        return self.dialog_state.get_log()


### Train ticketing chatbot

In [69]:
# Simulate a conversation for booking a train ticket
user_inputs = [
    "Can I change my booking to a later time?", # Modify reservation
    "Can I reschedule my ticket?",  # Modify reservation
    "Please cancel my ticket.",  # Cancel reservation
    "Can I remove my booking?", # Cancel reservation
    "I want to verify my reservation.", # Confirm reservation
    "Can I get my money back for this reservation?", # Request refund
    "What are the payment options available?", # Query payment options
    "Are pets allowed on the train?", # Query pet policy
    "I'd like to reserve a train ticket.", # Reservation request
    "Can you book a train to London for me?"  # Reservation request
]

In [72]:
# Initialize Chatbot with DialogState
dialog_state = DialogState(train_data)  # Pass the train data if needed
chatbot = Chatbot(dialog_state)

print("Train Ticket Booking Chatbot\n")
print("You can type your input below. Type 'exit' to end the conversation.\n")

while True:
    # Get user input
    user_input = input("You: ")
    
    # Check for exit condition
    if user_input.lower() == "exit":
        print("Ending the conversation. Goodbye!")
        break
    
    # Process the input and get chatbot response
    bot_response = chatbot.process_input(user_input)
    print(f"\nUser Input: {user_input}")
    print(f"Chatbot Response: {bot_response}")
    print(f"Current Dialogue State: {chatbot.get_dialogue_state()}\n")

# Print the final dialog state after the conversation ends
print("\nFinal Dialog State:")
print(chatbot.get_dialogue_state())
print("\nAll Dialogue Turns:")
for turn in chatbot.get_dialogue_turns():
    print(turn)


Train Ticket Booking Chatbot

You can type your input below. Type 'exit' to end the conversation.


User Input: Can I change my booking to a later time?
Chatbot Response:  Of course! To help you better, could you please provide me with some details about your booking such as the location, date, and time of the original reservation? This way, I can assist you in adjusting it to a later time that suits you best. Don't worry if you're not sure about all the details; any information you can give will help! 😊

Evidence: Mock data retrieved for intent 'modify_reservation' with details: {}
Current Dialogue State: {'intent': 'modify_reservation', 'entities': {'destination': 'a later time'}, 'context': {'last_response': " Of course! To help you better, could you please provide me with some details about your booking such as the location, date, and time of the original reservation? This way, I can assist you in adjusting it to a later time that suits you best. Don't worry if you're not sure abou

## Intents

### Intents From MultiWOZ

In [9]:
from datasets import load_dataset

# Load MultiWOZ 2.2 dataset with trust_remote_code
dataset = load_dataset("multi_woz_v22")

# Inspect the dataset
print(dataset)

DatasetDict({
    train: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 8437
    })
    validation: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 1000
    })
    test: Dataset({
        features: ['dialogue_id', 'services', 'turns'],
        num_rows: 1000
    })
})


In [10]:
train_data = dataset['train']
validation_data = dataset['validation']
test_data = dataset['test']

print(train_data[0])

{'dialogue_id': 'PMUL4398.json', 'services': ['restaurant', 'hotel'], 'turns': {'turn_id': ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11'], 'speaker': [0, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 1], 'utterance': ['i need a place to dine in the center thats expensive', 'I have several options for you; do you prefer African, Asian, or British food?', 'Any sort of food would be fine, as long as it is a bit expensive. Could I get the phone number for your recommendation?', 'There is an Afrian place named Bedouin in the centre. How does that sound?', 'Sounds good, could I get that phone number? Also, could you recommend me an expensive hotel?', "Bedouin's phone is 01223367660. As far as hotels go, I recommend the University Arms Hotel in the center of town.", 'Yes. Can you book it for me?', 'Sure, when would you like that reservation?', 'i want to book it for 2 people and 2 nights starting from saturday.', 'Your booking was successful. Your reference number is FRGZWQL2 . May I help you

In [11]:
intents = []

for dialogue in dataset['train']:
    turns = dialogue['turns']
    for i in range(len(turns['turn_id'])):
        # Access the 'frames' dictionary directly
        frame = turns['frames'][i]
        state = frame.get('state', [])
        
        if isinstance(state, list) and state:
            for s in state:
                intent = s.get('active_intent')
                if intent:
                    intents.append(intent)
                else:
                    print(f"No 'active_intent' in state: {s}")
        else:
            print(f"Missing or empty 'state' in frame: {frame}")

# Print unique intents and their counts
from collections import Counter
intent_counts = Counter(intents)
print("Extracted Intents:", intents)
print("Unique Intents:", len(intent_counts))
print("Intent Distribution:", intent_counts)


Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}
Missing or empty 'state' in frame: {'service': [], 'state': [], 'slots': []}

In [12]:
intent_counts

Counter({'find_restaurant': 10773,
         'find_hotel': 10540,
         'book_hotel': 4403,
         'book_restaurant': 4409,
         'find_taxi': 3695,
         'find_train': 9594,
         'book_train': 2409,
         'find_attraction': 8133,
         'find_police': 477,
         'find_hospital': 707,
         'find_bus': 8})

### Find Slots for Intents

In [13]:
from collections import defaultdict

# Dictionary to store intent-to-slots mapping
intent_to_slots = defaultdict(set)

# Iterate through the dataset
for dialogue in dataset['train']:
    turns = dialogue['turns']
    for i in range(len(turns['turn_id'])):
        frame = turns['frames'][i]  # Access the frame
        state = frame.get('state', [])
        
        if isinstance(state, list):
            for s in state:
                intent = s.get('active_intent')
                slots_values = s.get('slots_values', {})
                
                # Extract slot names and add them to the intent
                slot_names = slots_values.get('slots_values_name', [])
                for slot in slot_names:
                    intent_to_slots[intent].add(slot)

# Convert sets to lists for easier readability
intent_to_slots = {intent: list(slots) for intent, slots in intent_to_slots.items()}

# Print the mapping
for intent, slots in intent_to_slots.items():
    print(f"Intent: {intent}")
    print(f"Slots: {slots}")
    print()


Intent: find_restaurant
Slots: ['restaurant-bookpeople', 'restaurant-area', 'restaurant-pricerange', 'restaurant-booktime', 'restaurant-food', 'restaurant-name']

Intent: find_hotel
Slots: ['hotel-parking', 'hotel-pricerange', 'hotel-name', 'hotel-stars', 'hotel-area', 'hotel-internet', 'hotel-type']

Intent: book_hotel
Slots: ['hotel-parking', 'hotel-bookstay', 'hotel-pricerange', 'hotel-bookpeople', 'hotel-name', 'hotel-stars', 'hotel-area', 'hotel-internet', 'hotel-bookday', 'hotel-type']

Intent: book_restaurant
Slots: ['restaurant-bookpeople', 'restaurant-bookday', 'restaurant-pricerange', 'restaurant-area', 'restaurant-booktime', 'restaurant-food', 'restaurant-name']

Intent: find_taxi
Slots: ['taxi-leaveat', 'taxi-arriveby', 'taxi-departure', 'taxi-destination']

Intent: find_train
Slots: ['train-departure', 'train-leaveat', 'train-arriveby', 'train-bookpeople', 'train-destination', 'train-day']

Intent: book_train
Slots: ['train-departure', 'train-leaveat', 'train-arriveby', 't

## Chatbot Example

In [14]:
# Initialize DialogState and Chatbot
dialog_state = DialogState(train_data={})  # Provide training data if available
chatbot = Chatbot(dialog_state)

# Simulate user inputs
test_inputs = [
    "I want to book a hotel in the city center.",
    "Can you find me a train to New York?",
    "I need a taxi to the airport by 5 PM.",
]

# Process inputs and verify evidence storage
for user_input in test_inputs:
    bot_response = chatbot.process_input(user_input)
    print(f"User: {user_input}")
    print(f"Chatbot: {bot_response}")
    print(f"Retrieved Results So Far: {chatbot.dialog_state.retrieved_results}\n")


User: I want to book a hotel in the city center.
Chatbot:  Of course! Let's find you a great hotel in the city center. Could you please specify the city you'll be visiting? Also, it would be helpful if you could tell me your preferred dates of stay and any specific amenities or services that you require. I'm here to help you find the perfect accommodation for your trip!

Evidence: Mock data retrieved for intent 'reservation_request' with details: {}
Retrieved Results So Far: {'reservation_request': "Mock data retrieved for intent 'reservation_request' with details: {}"}

User: Can you find me a train to New York?
Chatbot:  Of course! I can help you with that. To provide the best options, could you please tell me which specific city in New York you're planning to visit and your preferred travel date(s) as well? For instance, are you looking to go to New York City (JFK Airport or Penn Station) on 11/7/2024? I can search for train schedules from there. If you need assistance with finding 

In [15]:
# Hotel Reservation Chatbot

# Initialize Chatbot with DialogState
dialog_state = DialogState(train_data={})  # Provide training data if available
chatbot = Chatbot(dialog_state)

# Simulate a conversation with hotel reservation-related inputs
user_inputs = [
    "I'd like to book a room for 2 people at 'The Grand Hotel' on 11/20/2024.",
    "Can I get a room with a sea view?",
    "Can you change the booking to 3 people?",
    "What is the check-in time?",
    "Thank you for your help!"
]

for i, user_input in enumerate(user_inputs):
    print(f"User Input {i+1}: {user_input}")
    bot_response = chatbot.process_input(user_input)
    print(f"Chatbot Response: {bot_response}\n")
    print(f"Current Dialogue Turn JSON: {chatbot.dialogue_turns[-1]}\n")
    print(f"Current Dialog State: {chatbot.get_dialogue_state()}\n")
    
# Display all dialogue turns and final state
print("\nAll Dialogue Turns:")
for turn in chatbot.get_dialogue_turns():
    print(turn)

print("\nFinal Dialog State:")
print(chatbot.get_dialogue_state())

User Input 1: I'd like to book a room for 2 people at 'The Grand Hotel' on 11/20/2024.
Chatbot Response:  Great! I can help you with that. Let me check the availability for The Grand Hotel on November 20, 2024, for two guests. How many nights would you like to stay? Also, do you have a preference for a room type or any specific amenities? I'll get back to you with some options as soon as possible. In the meantime, if there's anything else I can help you with, feel free to ask!

Evidence: Mock data retrieved for intent 'reservation_request' with details: {}

Current Dialogue Turn JSON: {"agent_utterance": " Great! I can help you with that. Let me check the availability for The Grand Hotel on November 20, 2024, for two guests. How many nights would you like to stay? Also, do you have a preference for a room type or any specific amenities? I'll get back to you with some options as soon as possible. In the meantime, if there's anything else I can help you with, feel free to ask!\n\nEvidenc

# Evaluation

transform the dataset format

In [132]:
import json

# Load the JSON file contents
file_path = '/Users/stella/Desktop/AB Capstone/DST/multiwoz/data/MultiWOZ_2.2/test/dialogues_001.json'

with open(file_path, 'r') as file:
    dialogues_data = json.load(file)

# Transformation function
def transform_to_evaluator_input(dialogues):
    """
    Transforms the dialogue data into the evaluator-friendly format.
    Each turn is extracted with relevant details and stored in a flat structure.
    """
    transformed_data = []
    for idx, dialogue in enumerate(dialogues):
        dialogue_id = idx  # Change dialogue_id to integer starting from 0
        turns = dialogue.get("turns", [])
        for turn in turns:
            transformed_data.append({
                "dialogue_id": dialogue_id,
                "turn_id": turn.get("turn_id"),
                "speaker": turn.get("speaker"),
                "utterance": turn.get("utterance"),
                "frames": turn.get("frames", [])
            })
    return transformed_data

# Transform the data
transformed_dialogues = transform_to_evaluator_input(dialogues_data)

# Save the transformed data for verification
output_path = '/Users/stella/Desktop/AB Capstone/DST/multiwoz/transformed_dialogues_001.json'
with open(output_path, 'w') as output_file:
    json.dump(transformed_dialogues, output_file, indent=4)

print(f"Transformed data saved to: {output_path}")


Transformed data saved to: /Users/stella/Desktop/AB Capstone/DST/multiwoz/transformed_dialogues_001.json


In [133]:
import json

# Load the extracted user utterances
input_file_path = '/Users/stella/Desktop/AB Capstone/DST/multiwoz/transformed_dialogues_001.json'

with open(input_file_path, 'r') as file:
    user_utterances = json.load(file)

# Step 1: Group turns by dialogue_id to form dialogues
dialogues = {}
for turn in user_utterances:
    dialogue_id = turn['dialogue_id']
    if dialogue_id not in dialogues:
        dialogues[dialogue_id] = []
    dialogues[dialogue_id].append(turn)

# Step 2: Extract the first two dialogues for testing
dialogue_ids = list(dialogues.keys())[:2]  # Get the first two dialogue IDs
test_dialogues = {dialogue_id: dialogues[dialogue_id] for dialogue_id in dialogue_ids}

# Step 3: Flatten the test dialogues into a list of turns
test_set = []
for dialogue_id in dialogue_ids:
    test_set.extend(dialogues[dialogue_id])

# Step 4: Save the test set to a JSON file
test_set_file_path = '/Users/stella/Desktop/AB Capstone/DST/multiwoz/test_set.json'
with open(test_set_file_path, 'w') as test_file:
    json.dump(test_set, test_file, indent=4)

print(f"Test set saved to: {test_set_file_path}")

Test set saved to: /Users/stella/Desktop/AB Capstone/DST/multiwoz/test_set.json


In [134]:
import json

# Load the provided JSON file
file_path = "/Users/stella/Desktop/AB Capstone/DST/multiwoz/test_set.json"
with open(file_path, "r") as file:
    dialogues_data = json.load(file)

# Extract user utterances with dialogue_id and turn_id
extracted_data = []
for dialogue in dialogues_data:
    if dialogue["speaker"] == "USER":
        extracted_data.append({
            "dialogue_id": dialogue["dialogue_id"],
            "turn_id": dialogue["turn_id"],
            "utterance": dialogue["utterance"]
        })

# Save the extracted data to a new JSON file
output_path = "/Users/stella/Desktop/AB Capstone/DST/multiwoz/extracted_user_utterances.json"
with open(output_path, "w") as output_file:
    json.dump(extracted_data, output_file, indent=4)

output_path


'/Users/stella/Desktop/AB Capstone/DST/multiwoz/extracted_user_utterances.json'

Run the chatbot and generate the reponses

In [140]:
# Step 5: Initialize the chatbot with its dialog state
dialog_state = DialogState(train_data={})  # Pass training data as needed
chatbot = Chatbot(dialog_state)

# Process the test set with the chatbot
current_dialogue_id = None

for turn in extracted_data:
    # Check if the dialogue_id changes
    if turn['dialogue_id'] != current_dialogue_id:
        # If a new dialogue_id is encountered
        current_dialogue_id = turn['dialogue_id']
        # Process the first turn of a new dialogue with `is_new_dialogue=True`
        is_new_dialogue = True
    else:
        is_new_dialogue = False

    # Feed the user utterance into the chatbot
    user_input = turn['utterance']
    chatbot.process_input(user_input, is_new_dialogue=is_new_dialogue)

print("Processing complete. Outputs saved by the chatbot.")


Processing complete. Outputs saved by the chatbot.


# Define evaluator

BLEU Score: The BLEU Score is computed by comparing the chatbot's generated utterances against the example dialogue (reference). It uses precision of n-grams (1 to 4 by default) with brevity penalty for shorter outputs.

1. filter out the dialogues turns from system and make into pairs (example vs. chatbot generated)
2. calculate bleu score for those pairs

In [125]:
import string
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction

class BLEUScorer:
    def __init__(self, chatbot_data, test_data):
        """
        Initialize BLEUScorer with chatbot and test datasets.
        """
        self.chatbot_data = chatbot_data
        self.test_data = test_data
        self.smooth = SmoothingFunction().method1  # Smoothing function for BLEU

    @staticmethod
    def preprocess(text):
        """
        Preprocess text by converting to lowercase, removing punctuation, and stripping whitespace.
        """
        return text.lower().translate(str.maketrans('', '', string.punctuation)).strip()

    def calculate_bleu_scores(self):
        """
        Calculate BLEU scores for chatbot responses compared to test data.
        Returns:
            average_bleu_score: Average BLEU score over all matched responses.
            paired_dialogues: List of dictionaries containing paired dialogues and BLEU scores.
        """
        # Normalize and filter system-generated responses from chatbot output
        chatbot_responses = [
            {
                "dialogue_id": int(chat["dialogue_id"]),
                "turn_id": int(chat["turn_id"]),
                "utterance": self.preprocess(chat["utterance"])
            }
            for chat in self.chatbot_data if chat["speaker"].lower() == "system"
        ]

        # Normalize and filter system turns from test dataset
        test_lookup = {
            (int(test["dialogue_id"]), int(test["turn_id"])): self.preprocess(test["utterance"])
            for test in self.test_data if test["speaker"].lower() == "system"
        }

        # Pair responses, calculate BLEU scores, and save paired dialogues for debugging
        bleu_scores = []
        paired_dialogues = []

        for response in chatbot_responses:
            key = (response["dialogue_id"], response["turn_id"])  # Ensure matching keys
            if key in test_lookup:
                reference = [test_lookup[key].split()]  # Tokenize reference
                hypothesis = response["utterance"].split()  # Tokenize chatbot response
                score = sentence_bleu(reference, hypothesis, smoothing_function=self.smooth)  # BLEU calculation
                bleu_scores.append(score)

                # Save paired dialogues for debugging
                paired_dialogues.append({
                    "dialogue_id": response["dialogue_id"],
                    "turn_id": response["turn_id"],
                    "chatbot_response": response["utterance"],
                    "reference_response": test_lookup[key],
                    "bleu_score": score
                })

        # Calculate average BLEU score
        average_bleu_score = sum(bleu_scores) / len(bleu_scores) if bleu_scores else 0

        return average_bleu_score, paired_dialogues

    def display_results(self, average_bleu_score, paired_dialogues):
        """
        Display BLEU scores and paired dialogues for debugging.
        """
        # Output paired dialogues for debugging
        for pair in paired_dialogues:
            print(f"Dialogue ID: {pair['dialogue_id']}, Turn ID: {pair['turn_id']}")
            print(f"Chatbot Response: {pair['chatbot_response']}")
            print(f"Reference Response: {pair['reference_response']}")
            print(f"BLEU Score: {pair['bleu_score']:.4f}")
            print("-" * 80)

        # Output average BLEU score
        print(f"Average BLEU Score: {average_bleu_score:.4f}")

Success Rate: Success Rate measures whether all requestable slots in the reference dialogue are provided in the generated dialogue.

1. Filter out the dialogues turns from user and make into pairs (example vs. chatbot generated)
2. Filter Test Data for Active Intent from example: Only consider frames where the active_intent is not NONE.
3. Match Entity Names with Slot Names: Compare the entities from the chatbot frame with the slot_values from the test frame for user turns.

In [146]:
class SuccessRateCalculator:
    def __init__(self, chatbot_data, test_data):
        """
        Initialize SuccessRateCalculator with chatbot and test datasets.
        """
        self.chatbot_data = chatbot_data
        self.test_data = test_data

    def calculate_success_rate(self):
        """
        Calculate the success rate based on slot names matching between
        chatbot entities and slot_values where active_intent is not NONE.
        
        Returns:
            success_rate: The proportion of successful turns.
        """
        successful_turns = 0
        total_turns = 0

        # Iterate through each turn in the test data where the speaker is "user"
        for test_turn in self.test_data:
            if test_turn["speaker"].lower() != "user":
                continue  # Skip non-user turns

            # Match dialogue_id and turn_id in chatbot_data
            chatbot_turns = [
                turn for turn in self.chatbot_data
                if turn["dialogue_id"] == test_turn["dialogue_id"]
                and turn["turn_id"] == int(test_turn["turn_id"])
            ]

            if chatbot_turns:
                chatbot_turn = chatbot_turns[0]  # Assume one matching turn

                # Process frames where active_intent is not NONE
                for test_frame in test_turn.get("frames", []):
                    state = test_frame.get("state", {})
                    if state.get("active_intent") == "NONE":
                        continue  # Skip frames with no active intent

                    # Extract slot_values from test data
                    slot_values = state.get("slot_values", {})

                    # Extract entities from chatbot data
                    chatbot_entities = chatbot_turn["frames"][0].get("entities", {})

                    # Compare slot names with entity names
                    if all(slot.split("-")[-1] in chatbot_entities for slot in slot_values.keys()):
                        successful_turns += 1
                        break  # Only count each turn once as successful

            # Increment total user turns
            total_turns += 1

        # Calculate success rate
        success_rate = successful_turns / total_turns if total_turns > 0 else 0
        return success_rate

Match Rate: Match Rate measures how many informable slots are correctly matched between the generated and reference dialogues.

1. Filter out the dialogues turns from user and make into pairs (example vs. chatbot generated)
2. Filter Test Data for Active Intent from example: Only consider frames where the active_intent is not NONE.
3. Matches are made between slot_values in the test data and entities in the chatbot data.

In [149]:
class MatchRateCalculator:
    def __init__(self, chatbot_data, test_data):
        """
        Initialize MatchRateCalculator with chatbot and test datasets.
        """
        self.chatbot_data = chatbot_data
        self.test_data = test_data

    def calculate_match_rate(self):
        """
        Calculate the match rate based on slot values matching between chatbot and test data.
        Returns:
            match_rate: The proportion of matched slots.
        """
        total_slots = 0
        matched_slots = 0

        # Iterate through test turns where the speaker is "user"
        for test_turn in self.test_data:
            if test_turn["speaker"].lower() != "user":
                continue  # Skip non-user turns

            # Extract dialogue_id and turn_id for pairing
            test_dialogue_id = int(test_turn["dialogue_id"])
            test_turn_id = int(test_turn["turn_id"])

            # Iterate through frames with a non-NONE active_intent
            for test_frame in test_turn.get("frames", []):
                state = test_frame.get("state", {})
                if state.get("active_intent") == "NONE":
                    continue  # Skip frames with no active intent

                # Extract slot_values from the test frame
                test_slot_values = state.get("slot_values", {})

                # Find corresponding turn in chatbot data
                corresponding_turn = next(
                    (turn for turn in self.chatbot_data
                     if turn["dialogue_id"] == test_dialogue_id and turn["turn_id"] == test_turn_id),
                    None
                )

                # Extract chatbot entities
                chatbot_entities = {}
                if corresponding_turn:
                    chatbot_frames = corresponding_turn.get("frames", [])
                    if chatbot_frames:
                        chatbot_entities = chatbot_frames[0].get("entities", {})

                # Compare slot values with chatbot entities
                for slot, values in test_slot_values.items():
                    total_slots += 1
                    # Map slot key to expected entity key
                    entity_key = slot.split("-")[-1]  # Remove domain prefix
                    if entity_key in chatbot_entities and chatbot_entities[entity_key] in values:
                        matched_slots += 1

        # Calculate match rate
        match_rate = matched_slots / total_slots if total_slots > 0 else 0
        return match_rate

# Evaluator usage

load the test dialogue set-001 from multiwoz

In [142]:
import json

# Load files
with open('/Users/stella/Desktop/AB Capstone/DST/multiwoz/chatbot_output.json', 'r') as chatbot_file:
    chatbot_data = json.load(chatbot_file)

with open('/Users/stella/Desktop/AB Capstone/DST/multiwoz/test_set.json', 'r') as test_file:
    test_data = json.load(test_file)

bleu_score

In [151]:
# Initialize the BLEUScorer class with chatbot_data and test_data
bleu_scorer = BLEUScorer(chatbot_data, test_data)

# Calculate BLEU scores
average_bleu_score, paired_dialogues = bleu_scorer.calculate_bleu_scores()

# Display the results
bleu_scorer.display_results(average_bleu_score, paired_dialogues)

Dialogue ID: 0, Turn ID: 1
Chatbot Response: of course to make things easier for you ill help you book your train tickets from norwich to cambridge for november 5th 2024 let me check the available trains and get back to you shortly

in the meantime if you have any questions about local attractions in cambridge or need suggestions on restaurants or hotels feel free to ask im here to help make your trip as smooth as possible

stay tuned for more updates on your train reservations 😊

evidence mock data retrieved for intent trainschedule with details
Reference Response: i have 133 trains matching your request is there a specific day and time you would like to travel
BLEU Score: 0.0032
--------------------------------------------------------------------------------
Dialogue ID: 0, Turn ID: 3
Chatbot Response: great let me help you plan your trip for next monday november 11th 2024 to ensure that you arrive by 6 pm local time at your destination well need to figure out the departing city and 

success_rate

In [147]:
# Initialize the SuccessRateCalculator class with chatbot_data and test_data
success_calculator = SuccessRateCalculator(chatbot_data, test_data)

# Calculate the success rate
success_rate = success_calculator.calculate_success_rate()

# Output the result
print(f"Success Rate: {success_rate:.2%}")

Success Rate: 20.00%


match_rate

In [150]:
# Initialize the MatchRateCalculator class with chatbot_data and test_data
match_calculator = MatchRateCalculator(chatbot_data, test_data)

# Calculate the match rate
match_rate = match_calculator.calculate_match_rate()

# Output the result
print(f"Match Rate: {match_rate:.2%}")

Match Rate: 10.81%
